# Демонстрация simple_llm
## Полное руководство по установке и использованию

## 1. Установка и настройка

### Клонирование репозитория:
```bash
git clone https://github.com/ваш_username/simple-llm.git
cd simple-llm
```

### Установка зависимостей:
```bash
pip install -e .
pip install torch tqdm
```

### Проверка структуры данных:
```bash
mkdir -p data/corpus/sample data/model data/tokenizer
```

## 2. Инициализация и проверка окружения

In [ ]:
import sys
import os
import torch

# Проверка версии PyTorch
print(f"PyTorch version: {torch.__version__}")

# Добавление пути к библиотеке
project_path = os.path.abspath('../simple-llm')
sys.path.append(project_path)
print(f"Путь к проекту: {project_path}")

# Проверка модулей
try:
    from simple_llm.tokenizer.bpe import BPETokenizer
    from simple_llm.data.get_data import load_text_corpus
    from simple_llm.transformer.gpt import GPT
    print("✓ Все модули успешно импортированы")
except ImportError as e:
    print(f"✗ Ошибка: {e}")
    print("Решение: выполните 'pip install -e .' из корня проекта")

## 3. Работа с токенизатором

In [ ]:
# Инициализация токенизатора
tokenizer = BPETokenizer()

# Загрузка и обработка текста
corpus_path = 'data/corpus/sample/'
if os.path.exists(corpus_path):
    text = load_text_corpus(corpus_path)
    print(f"Загружено текста: {len(text.split())} слов")
    
    # Обучение токенизатора
    tokenizer.train(text, vocab_size=1000)
    print(f"Токенизатор обучен, размер словаря: {tokenizer.vocab_size}")
    
    # Тест токенизации
    test_phrase = "Пример работы токенизатора"
    tokens = tokenizer.encode(test_phrase)
    print(f"Текст: {test_phrase}")
    print(f"Токены: {tokens}")
    print(f"Обратное преобразование: {tokenizer.decode(tokens)}")
else:
    print(f"Директория {corpus_path} не содержит данных для обучения")
    print("Добавьте текстовые файлы в формате .txt в эту директорию")

## 4. Подготовка данных для обучения

In [ ]:
if 'text' in locals():
    # Токенизация всего корпуса
    all_tokens = tokenizer.encode(text)
    
    # Создание обучающих последовательностей
    seq_length = 64
    examples = []
    for i in range(0, len(all_tokens) - seq_length - 1, seq_length):
        input_seq = all_tokens[i:i+seq_length]
        target_seq = all_tokens[i+1:i+seq_length+1]
        examples.append((input_seq, target_seq))
    
    print(f"Создано обучающих примеров: {len(examples)}")
    print(f"Размер последовательности: {seq_length} токенов")
    print(f"Пример входных данных: {examples[0][0][:10]}...")
    print(f"Пример целевых данных: {examples[0][1][:10]}...")
else:
    print("Невозможно подготовить данные: текст не загружен")

## 5. Обучение модели GPT

In [ ]:
if 'examples' in locals() and len(examples) > 0:
    # Конфигурация модели
    config = {
        'vocab_size': tokenizer.vocab_size,
        'embed_dim': 128,
        'num_heads': 4,
        'num_layers': 3,
        'max_len': seq_length
    }
    
    # Инициализация модели
    model = GPT(config)
    optimizer = optim.Adam(model.parameters(), lr=0.001)
    criterion = torch.nn.CrossEntropyLoss()
    
    # Процесс обучения
    num_epochs = 5
    batch_size = 8
    
    for epoch in range(num_epochs):
        total_loss = 0
        model.train()
        
        for i in range(0, len(examples), batch_size):
            batch = examples[i:i+batch_size]
            inputs = torch.tensor([ex[0] for ex in batch])
            targets = torch.tensor([ex[1] for ex in batch])
            
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs.view(-1, config['vocab_size']), targets.view(-1))
            loss.backward()
            optimizer.step()
            
            total_loss += loss.item()
        
        avg_loss = total_loss / (len(examples) / batch_size)
        print(f"Эпоха {epoch+1}/{num_epochs}, Loss: {avg_loss:.4f}")
    
    print("Обучение завершено!")
else:
    print("Невозможно начать обучение: нет подготовленных данных")

## 6. Генерация текста

In [ ]:
def generate_text(model, tokenizer, prompt, max_len=50, temperature=0.7):
    model.eval()
    tokens = tokenizer.encode(prompt)
    
    for _ in range(max_len):
        input_ids = torch.tensor([tokens[-config['max_len']:]])
        with torch.no_grad():
            logits = model(input_ids)[0, -1, :] / temperature
        probs = torch.softmax(logits, dim=-1)
        next_token = torch.multinomial(probs, num_samples=1).item()
        tokens.append(next_token)
    
    return tokenizer.decode(tokens)

if 'model' in locals():
    prompts = [
        "Сегодня прекрасный день,",
        "Искусственный интеллект",
        "В далеком будущем"
    ]
    
    for prompt in prompts:
        generated = generate_text(model, tokenizer, prompt)
        print(f"Промпт: '{prompt}'")
        print(f"Результат: {generated}\n")
else:
    print("Модель не обучена, генерация невозможна")

## 7. Сохранение и загрузка моделей

In [ ]:
def save_model(model, tokenizer, model_name):
    model_path = f"data/model/{model_name}.pth"
    tokenizer_path = f"data/tokenizer/{model_name}_tokenizer.json"
    
    torch.save(model.state_dict(), model_path)
    tokenizer.save(tokenizer_path)
    print(f"Модель сохранена в {model_path}")
    print(f"Токенизатор сохранен в {tokenizer_path}")

def load_model(model_name, config):
    model_path = f"data/model/{model_name}.pth"
    tokenizer_path = f"data/tokenizer/{model_name}_tokenizer.json"
    
    model = GPT(config)
    model.load_state_dict(torch.load(model_path))
    
    tokenizer = BPETokenizer()
    tokenizer.load(tokenizer_path)
    
    print(f"Модель загружена из {model_path}")
    return model, tokenizer

# Пример использования:
# save_model(model, tokenizer, "my_first_model")
# loaded_model, loaded_tokenizer = load_model("my_first_model", config)

## 8. Советы по улучшению

1. Для лучших результатов:
   - Увеличьте размер корпуса
   - Добавьте больше эпох обучения
   - Настройте параметры модели

2. Экспериментируйте с:
   - Температурой генерации (0.1-1.0)
   - Разными промптами
   - Архитектурой модели

3. Дополнительные возможности:
   - Визуализация attention-карт
   - Реализация beam search
   - Fine-tuning на специфичных данных